In [1]:
import cupy as cp
import numpy as np
from time import perf_counter
from pyqcu import define
from pyqcu import io
from pyqcu import qcu
import cupyx.scipy.sparse.linalg as csla
from typing import Callable, Tuple, List

print('My rank is ', define.rank)


    @@@@@@######QCU NOTES START######@@@@@@@
    1. The libqcu.so was compiled when pyqcu setup in download_path/PyQCU/lib, please add this path to your LD_LIBRARY_PATH.
    2. The QCU(PyQCU) splite grid by x->y->z->t, lattice by x->y->z->t->p->d->c->c or x->y->z->t->c->s(->p) and x->y->z->t->c->s->c->s(->p).
    3. The QUDA(PyQUDA) splite grid by t->z->y->x, lattice by c->c->x->y->z->t->p->d or c->s->x->y->z->t(->p) and c->s->c->s->x->y->z->t(->p).
    4. The QCU input params in numpy array(dtype=np.int32), argv in  numpy array(dtype=np.float32 or float64) array, set_ptrs in numpy array(dtype=np.int64), other in cupy array(dtype=cp.complex64 or complex128).
    5. The smallest lattice size is (x=4,y=4,z=4,t=8) that QCU support.
    @@@@@@######QCU NOTES END######@@@@@@@
    
My rank is  0


In [2]:
params = np.array([0]*define._PARAMS_SIZE_, dtype=np.int32)
params[define._LAT_X_] = 24
params[define._LAT_Y_] = 24
params[define._LAT_Z_] = 24
params[define._LAT_T_] = 32
params[define._LAT_XYZT_] = params[define._LAT_X_] * params[define._LAT_Y_] * params[define._LAT_Z_] * params[define._LAT_T_]
params[define._GRID_X_] = 1
params[define._GRID_Y_] = 1
params[define._GRID_Z_] = 1
params[define._GRID_T_] = 1
params[define._PARITY_] = 0
params[define._NODE_RANK_] = 0
params[define._NODE_SIZE_] = 1
params[define._DAGGER_] = 0
params[define._MAX_ITER_] = 1e4
params[define._DATA_TYPE_] = 0
params[define._SET_INDEX_] = 2
params[define._SET_PLAN_] = 0
argv = np.array([0.0]*define._ARGV_SIZE_, dtype=np.float32)
argv[define._MASS_] = 0.0
argv[define._TOL_] = 1e-9
print("Parameters:", params)
print("Arguments:", argv)

Parameters: [    24     24     24     32 442368      1      1      1      1      0
      0      1      0  10000      0      2      0]
Arguments: [0.e+00 1.e-09]


In [3]:
# gauge_filename = f"quda_wilson-dslash-gauge_-{params[define._LAT_X_]}-{params[define._LAT_Y_]}-{params  [define._LAT_Z_]}-{params[define._LAT_T_]}-{params[define._LAT_XYZT_]}-{params[define._GRID_X_]}-{params[define._GRID_Y_]}-{params[define._GRID_Z_]}-{params[define._GRID_T_]}-{params[define._PARITY_]}-{params[define._NODE_RANK_]}-{params[define._NODE_SIZE_]}-{params[define._DAGGER_]}-f.bin"
gauge_filename = f"beta6.20_mu-0.2770_ms-0.2310_L24x64_cfg_10000.bin"
print("Gauge filename:", gauge_filename)
gauge = cp.fromfile(gauge_filename, dtype=cp.complex128,
                    count=params[define._LAT_XYZT_]*define._LAT_DCC_)
gauge = io.gauge2tzyxdcc(gauge, params)
print("Gauge:", gauge)
print("Gauge data:", gauge.data)
print("Gauge shape:", gauge.shape)

Gauge filename: beta6.20_mu-0.2770_ms-0.2310_L24x64_cfg_10000.bin
U: [ 0.380847  -0.15622665j -0.5222466 +0.5953112j  -0.3945818 -0.21844235j
 -0.24793721+0.32244315j  0.2978312 +0.45352106j  0.29559142-0.67290303j
  0.26466566-0.77140031j  0.16081703-0.22938215j  0.24674984-0.4421876j ]
_U: [0.        +0.j         0.        +0.j         0.        +0.j
 0.        +0.j         0.        +0.j         0.        +0.j
 0.26466566-0.77140033j 0.16081703-0.22938214j 0.24674985-0.4421876j ]
Gauge: 15925248
Gauge: [[[[[[[ 3.80847001e-01-1.56226647e-01j
       -5.22246602e-01+5.95311199e-01j
       -3.94581802e-01-2.18442353e-01j]
      [-2.47937212e-01+3.22443146e-01j
        2.97831204e-01+4.53521058e-01j
        2.95591423e-01-6.72903032e-01j]
      [ 2.64665661e-01-7.71400311e-01j
        1.60817029e-01-2.29382149e-01j
        2.46749845e-01-4.42187601e-01j]]

     [[-5.73769807e-01-6.80440650e-01j
       -1.24949824e-01-1.86966643e-01j
       -3.93886803e-01-4.55294760e-02j]
      [ 3.99971

In [54]:
set_ptrs = np.array(params, dtype=np.int64)
print("Set pointers:", set_ptrs)
print("Set pointers data:", set_ptrs.data)
qcu.applyInitQcu(set_ptrs, params, argv)

Set pointers: [     32      32      32      32 1048576       1       1       1       1
       0       0       1       0   10000       0       2       0]
Set pointers data: <memory at 0x7f4f1e196ec0>
gridDim.x               :4096
blockDim.x              :128
host_params[_LAT_X_]    :16
host_params[_LAT_Y_]    :32
host_params[_LAT_Z_]    :32
host_params[_LAT_T_]    :32
host_params[_LAT_XYZT_] :524288
host_params[_GRID_X_]   :1
host_params[_GRID_Y_]   :1
host_params[_GRID_Z_]   :1
host_params[_GRID_T_]   :1
host_params[_PARITY_]   :0
host_params[_NODE_RANK_]:0
host_params[_NODE_SIZE_]:1
host_params[_DAGGER_]   :0
host_params[_MAX_ITER_] :10000
host_params[_SET_INDEX_]:2
host_params[_SET_PLAN_] :0
host_argv[_MASS_]       :0.000000e+00
host_argv[_TOL_]        :1.000000e-09
lat_2dim[_XY_]          :512
lat_2dim[_XZ_]          :512
lat_2dim[_XT_]          :512
lat_2dim[_YZ_]          :1024
lat_2dim[_YT_]          :1024
lat_2dim[_ZT_]          :1024
lat_3dim[_YZT_]         :32768
lat_3dim[_XZT

In [55]:
# give x, b, r, r_tilde, p, v, s, t
lat_t = params[define._LAT_T_]
lat_z = params[define._LAT_Z_]
lat_y = params[define._LAT_Y_]
lat_x = int(params[define._LAT_X_]/define._LAT_P_)
lat_d = define._LAT_D_
lat_s = define._LAT_S_
lat_p = define._LAT_P_
lat_c = define._LAT_C_
latt_shape = (lat_s, lat_c, lat_t, lat_z, lat_y, lat_x)
MAX_ITER = params[define._MAX_ITER_]
TOL = argv[define._TOL_]
N = params[define._LAT_XYZT_] * define._LAT_HALF_SC_
params[define._LAT_E_] = 10
max_eigen_value = 1.0
scale = 1e0

In [56]:
def _matvec(src):
    print("norm src", cp.linalg.norm(src))
    dest = cp.zeros(N, cp.complex64)
    qcu.applyWilsonCgDslashQcu(dest, src, gauge, set_ptrs, params)
    print("norm dest", cp.linalg.norm(dest))
    return dest


def __matvec(src, max_eigen_value=max_eigen_value, scale=scale):
    print("norm src", cp.linalg.norm(src))
    dest = cp.zeros(N, cp.complex64)
    qcu.applyWilsonCgDslashQcu(dest, src, gauge, set_ptrs, params)
    print("norm dest", cp.linalg.norm(dest))
    return max_eigen_value*src-scale*dest

In [57]:
# def power_iteration(matvec, v0, num_iter=params[define._MAX_ITER_], tol=argv[define._TOL_]):
#     v = v0
#     for i in range(num_iter):
#         Av = matvec(v)
#         v_new = Av / cp.linalg.norm(Av)
#         diff = cp.linalg.norm(v_new - v)
#         print(f"Iteration {i+1}: difference = {diff:.6e}")
#         if diff < tol:
#             print(
#                 f"Power Iteration converged after {i+1} iterations. Difference: {diff:.6e}")
#             break
#         v = v_new
#     eigenvalue = cp.dot(v.conj().T, matvec(v))
#     return eigenvalue, v
# def validate_power_iteration():
#     v0 = cp.random.randn(N).astype(cp.complex64)
#     eigenvalue, eigenvector = power_iteration(_matvec, v0)
#     print("Dominant eigenvalue:", eigenvalue)
#     print("Corresponding eigenvector:", eigenvector[:10])
#     Ax = _matvec(eigenvector)
#     eigenvalue_check = cp.dot(eigenvector.conj().T, Ax)
#     print(f"Eigenvalue verification (v^T A v): {eigenvalue_check}")
#     if cp.isclose(eigenvalue, eigenvalue_check):
#         print("Validation passed: Eigenvalue calculation is correct.")
#     else:
#         print("Validation failed: Eigenvalue calculation is incorrect.")
#     print("Eigenvector norm:", cp.linalg.norm(eigenvector))
#     return eigenvalue, eigenvector
# eigenvalue, eigenvector = validate_power_iteration()
# print("Diff:", cp.linalg.norm(_matvec(eigenvector) -
#       eigenvalue*eigenvector) / cp.linalg.norm(eigenvector))

In [58]:
# print("Eigenvalue:", eigenvalue)

In [59]:
# # bistabcg
# def dot(a, b):
#     cp.cuda.runtime.deviceSynchronize()
#     return cp.inner(a.flatten().conjugate(), b.flatten())


# def diff(a, b):
#     cp.cuda.runtime.deviceSynchronize()
#     return cp.linalg.norm(a - b) / cp.linalg.norm(b)


# def run(eigen_value):
#     t0 = perf_counter()
#     x = cp.random.rand(N).astype(cp.complex64)
#     print("shape:", x.shape)
#     b = cp.zeros(N, cp.complex64)  # must be zero
#     r = cp.zeros(N, cp.complex64)
#     r_tilde = cp.zeros(N, cp.complex64)
#     p = cp.zeros(N, cp.complex64)
#     s = cp.zeros(N, cp.complex64)
#     v = cp.zeros(N, cp.complex64)
#     t = cp.zeros(N, cp.complex64)
#     r = b - _matvec(x, eigen_value)
#     r_tilde = r
#     r_norm2 = 0
#     rho_prev = 1
#     rho = 0
#     alpha = 1
#     omega = 1
#     beta = 0
#     for i in range(MAX_ITER):
#         # print("## rho:", rho)
#         rho = dot(r_tilde, r)
#         # print("## beta:", beta)
#         beta = (rho / rho_prev) * (alpha / omega)
#         p = r + (p - v * omega) * beta
#         # v = A * p
#         v = _matvec(p, eigen_value)
#         # print("## alpha:", alpha)
#         alpha = rho / dot(r_tilde, v)
#         s = r - v * alpha
#         # t = A * s
#         t = _matvec(s, eigen_value)
#         # print("## omega:", omega)
#         omega = dot(t, s) / dot(t, t)
#         x = x + p * alpha + s * omega
#         r = s - t * omega
#         r_norm2 = cp.linalg.norm(r)
#         print("##{}# r_norm2:{}".format(i, r_norm2))
#         _diff = diff(_matvec(x, 0.0), eigen_value*x)
#         print("diff:", _diff)
#         # break
#         # if (r_norm2 < TOL or i == MAX_ITER - 1):
#         #     print("### turns:", i)
#         #     break
#         if (_diff < TOL or i == MAX_ITER - 1):
#             print("### turns:", i)
#             break
#         rho_prev = rho
#     # print(" diff:", diff(_matvec(x, eigen_value), b))
#     # print("x:", x)
#     t1 = perf_counter()
#     print("Time:", t1-t0)
#     return x, _diff


# eigen_value = eigenvalue
# eigen_vector, _diff = run(eigen_value)
# print("eigen_vector:", eigen_vector)
# print("eigen_vector shape:", eigen_vector.shape)
# print("diff:", _diff)

In [60]:
# print("Difference:", cp.linalg.norm(eigenvector-eigen_vector)/cp.linalg.norm(eigenvector))

In [61]:
# import cupyx.scipy.sparse.linalg as csla
# params[define._LAT_E_] = 24
# A = csla.LinearOperator((N,
#                         N), matvec=_matvec, dtype=cp.complex64)
# evals, evecs = csla.eigsh(a=A, k=params[define._LAT_E_], which="SA",
#                           return_eigenvectors=True)
# print("evals:", evals)
# print("evecs:", evecs)
# cp.linalg.norm(_matvec(evecs[:, 0])-evals[0] *
#                evecs[:, 0])/cp.linalg.norm(evals[0]*evecs[:, 0])

In [62]:
def shifted_power_iteration(
    matvec,
    n=N,
    num_eigenvalues=params[define._LAT_E_],
    max_iter=params[define._MAX_ITER_],
    tol=argv[define._TOL_]
):
    eigenvalues = []
    eigenvectors = []
    # Buffer for intermediate results
    v = cp.ndarray((n,), dtype=np.complex64)
    w = cp.ndarray((n,), dtype=np.complex64)
    # Store cumulative shift
    total_shift = 0.0

    for k in range(num_eigenvalues):
        # Initialize random vector
        v[:] = cp.random.rand(n) + 1j * cp.random.rand(n)
        # Orthogonalize against previously found eigenvectors
        for j in range(k):
            projection = cp.dot(cp.conj(eigenvectors[j]), v)
            v -= projection * eigenvectors[j]
        # Normalize
        v /= cp.linalg.norm(v)

        # Power iteration
        eigenvalue = None
        for iter_count in range(max_iter):
            # Matrix-vector multiplication
            w = matvec(v)
            # Apply shift
            w += total_shift * v
            # Calculate Rayleigh quotient
            new_eigenvalue = cp.dot(cp.conj(v), w)
            # Normalize
            norm = cp.linalg.norm(w)
            if norm < tol:  # Avoid zero vector
                v[:] = cp.random.rand(n) + 1j * cp.random.rand(n)
                continue
            w /= norm

            # Check convergence
            if eigenvalue is not None:
                diff = abs(new_eigenvalue - eigenvalue)
                print(f"Iteration {iter_count} for eigenvalue {k}: {diff:.8f}")
                if diff < tol:
                    break
            eigenvalue = new_eigenvalue
            v[:] = w

        # Store results and subtract shift
        if eigenvalue is not None:
            eigenvalue -= total_shift
            eigenvalues.append(eigenvalue)
            eigenvectors.append(v.copy())
            # Update shift for next eigenvalue
            total_shift = eigenvalue.real

    return eigenvalues, eigenvectors


# Calculate eigenvalues and eigenvectors
eigenvalues, eigenvectors = shifted_power_iteration(__matvec)

# Verify results
print("Computed eigenvalues:")
for i, ev in enumerate(eigenvalues):
    print(f"λ_{i} = {ev:.8f}")
    # Verify eigenvector
    v = eigenvectors[i]
    w = cp.zeros_like(v)
    w = __matvec(v)
    error = cp.linalg.norm(w - ev * v) / cp.linalg.norm(w)
    print(f"Relative error: {error:.2e}")

norm src 1.0
norm dest 0.5633586
norm src 0.9999999
norm dest 0.17303562
Iteration 1 for eigenvalue 0: 0.25194073
norm src 0.99999994
norm dest 0.06454282
Iteration 2 for eigenvalue 0: 0.02132064
norm src 1.0
norm dest 0.02759348
Iteration 3 for eigenvalue 0: 0.00290704
norm src 0.99999994
norm dest 0.013232366
Iteration 4 for eigenvalue 0: 0.00056732
norm src 1.0
norm dest 0.0071789986
Iteration 5 for eigenvalue 0: 0.00015336
norm src 0.99999994
norm dest 0.004459412
Iteration 6 for eigenvalue 0: 0.00005627
norm src 0.99999994
norm dest 0.0031343827
Iteration 7 for eigenvalue 0: 0.00002652
norm src 1.0
norm dest 0.0024111238
Iteration 8 for eigenvalue 0: 0.00001508
norm src 0.99999994
norm dest 0.001965961
Iteration 9 for eigenvalue 0: 0.00000894
norm src 0.99999994
norm dest 0.0016649711
Iteration 10 for eigenvalue 0: 0.00000608
norm src 0.99999994
norm dest 0.0014486677
Iteration 11 for eigenvalue 0: 0.00000423
norm src 1.0
norm dest 0.0012873419
Iteration 12 for eigenvalue 0: 0.000

In [63]:
eigenvalues

[array(0.999352+4.092726e-12j, dtype=complex64),
 array(0.9993112-2.842171e-11j, dtype=complex64),
 array(0.99930155-1.36424205e-11j, dtype=complex64),
 array(0.99930274-1.7223556e-11j, dtype=complex64),
 array(0.9992995+2.3646862e-11j, dtype=complex64),
 array(0.9992949-2.7284841e-11j, dtype=complex64),
 array(0.99930775-1.6370905e-11j, dtype=complex64),
 array(0.99929833+5.684342e-12j, dtype=complex64),
 array(0.9992943+9.094947e-12j, dtype=complex64),
 array(0.99930155+3.637979e-12j, dtype=complex64)]

In [64]:
eigenvectors[0]

array([0.0002671 +0.00033389j, 0.00026914+0.0003151j ,
       0.00023126+0.00029412j, ..., 0.00031721+0.00026323j,
       0.00030408+0.00028839j, 0.00029509+0.00026849j], dtype=complex64)

In [65]:
eigenvectors[1]

array([0.00028195+4.8963167e-04j, 0.00023728+5.5122568e-04j,
       0.00019183+5.4973154e-04j, ..., 0.00023719+9.2579130e-06j,
       0.00024886+1.4722072e-05j, 0.00025686+2.9678380e-05j],
      dtype=complex64)

In [66]:
eigenvectors[2]

array([ 4.4447475e-05-0.00025679j,  2.8910108e-05-0.00019618j,
        3.8629183e-05-0.00020872j, ..., -4.1275544e-04+0.00027719j,
       -4.3412173e-04+0.00034372j, -4.6717291e-04+0.00031947j],
      dtype=complex64)

In [67]:
eigenvectors[3]

array([-0.00016995-0.00061296j, -0.00017453-0.00065493j,
       -0.00017066-0.00064561j, ...,  0.00071686+0.00019863j,
        0.00069974+0.00022698j,  0.00067599+0.00016768j], dtype=complex64)

In [68]:
eigen_index = 8
print("Diff:", cp.linalg.norm(__matvec(eigenvectors[eigen_index]) -
      eigenvalues[eigen_index]*eigenvectors[eigen_index]) / cp.linalg.norm(eigenvectors[eigen_index]))

norm src 0.99999994
norm dest 0.0010279338
Diff: 0.0007478467


In [69]:
for i, ev in enumerate(eigenvalues):
    print(f"λ_{i} = {ev:.8f}")
    # 验证本征向量
    v = eigenvectors[i]*1e6
    print(f"v_{i} = {v}")
    w = cp.zeros_like(v)
    w = __matvec(v)
    print(f"w_{i} = {w}")
    print(f"ev_{i} * v_{i} = {ev*v}")
    error = cp.linalg.norm(w - ev * v) / cp.linalg.norm(w)
    print(f"相对误差: {error:.2e}")
    j = i+1
    if i == len(eigenvalues)-1:
        j = 0
    eigen_diff = cp.linalg.norm(
        eigenvectors[i]-eigenvectors[j])/cp.linalg.norm(eigenvectors[i])
    print(f"本征向量{i}与本征向量{j}的相对误差:{eigen_diff:.2e}")

λ_0 = 0.99935198+0.00000000j
v_0 = [267.09796+333.8945j  269.13684+315.10092j 231.26216+294.1191j  ...
 317.20602+263.2326j  304.07687+288.38812j 295.08658+268.49258j]
norm src 1000000.0
norm dest 690.2009
w_0 = [266.9322 +333.77026j 268.92105+314.9904j  231.01994+294.02377j ...
 316.99527+263.01987j 303.8574 +288.14618j 294.9059 +268.27548j]
ev_0 * v_0 = [266.92487+333.67813j 268.96243+314.89673j 231.1123 +293.92853j ...
 317.00046+263.062j   303.87982+288.20123j 294.89536+268.3186j ]
相对误差: 2.38e-04
本征向量0与本征向量1的相对误差:1.43e+00
λ_1 = 0.99931121-0.00000000j
v_1 = [281.9473 +489.63165j  237.27559+551.22565j  191.82562+549.73157j  ...
 237.19228  +9.257913j 248.85745 +14.722072j 256.8562  +29.678381j]
norm src 999999.94
norm dest 937.0313
w_1 = [281.68896+489.45572j  237.002  +551.00977j  191.5666 +549.51184j  ...
 236.95976  +9.440759j 248.6424  +14.866237j 256.6577  +29.782452j]
ev_1 * v_1 = [281.75308+489.2944j   237.11215+550.84595j  191.6935 +549.3529j   ...
 237.0289   +9.251535j 248.

In [70]:
_eigenvalues = (max_eigen_value -
                cp.array(eigenvalues, dtype=cp.complex64))/scale
_eigenvectors = cp.array(eigenvectors, dtype=cp.complex64)

In [71]:
print("_eigenvalues:", _eigenvalues)

_eigenvalues: [0.00064802-4.09272616e-12j 0.00068879+2.84217094e-11j
 0.00069845+1.36424205e-11j 0.00069726+1.72235559e-11j
 0.00070047-2.36468622e-11j 0.00070512+2.72848411e-11j
 0.00069225+1.63709046e-11j 0.00070167-5.68434189e-12j
 0.00070572-9.09494702e-12j 0.00069845-3.63797881e-12j]


In [72]:
print("_eigenvectors.shape:", _eigenvectors.shape)
print(_eigenvectors)

_eigenvectors.shape: (10, 6291456)


[[ 2.6709796e-04+3.3389451e-04j  2.6913683e-04+3.1510092e-04j
   2.3126217e-04+2.9411912e-04j ...  3.1720602e-04+2.6323259e-04j
   3.0407688e-04+2.8838811e-04j  2.9508659e-04+2.6849259e-04j]
 [ 2.8194729e-04+4.8963167e-04j  2.3727558e-04+5.5122568e-04j
   1.9182562e-04+5.4973154e-04j ...  2.3719227e-04+9.2579130e-06j
   2.4885745e-04+1.4722072e-05j  2.5685620e-04+2.9678380e-05j]
 [ 4.4447475e-05-2.5679413e-04j  2.8910108e-05-1.9617518e-04j
   3.8629183e-05-2.0871613e-04j ... -4.1275544e-04+2.7718701e-04j
  -4.3412173e-04+3.4371600e-04j -4.6717291e-04+3.1946774e-04j]
 ...
 [-2.7962765e-04-3.3694920e-05j -2.3521746e-04-4.9677117e-05j
  -2.5011116e-04-4.5450208e-05j ...  6.7690776e-06+4.6008552e-04j
   2.4151486e-05+4.1721202e-04j  6.1881023e-05+4.2502498e-04j]
 [ 1.7638311e-04-1.2020739e-04j  1.7795042e-04-8.5920736e-05j
   1.9414365e-04-1.0706434e-04j ...  6.6649016e-05-4.6800458e-05j
   8.1694423e-05-6.2304491e-05j  1.1545337e-04-1.1300186e-04j]
 [-3.3316968e-04-2.5975078e-04j -2.92095

In [73]:

for i, ev in enumerate(_eigenvalues):
    print(f"λ_{i} = {ev:.8f}")
    # 验证本征向量
    v = _eigenvectors[i]
    print(f"v_{i} = {v}")
    w = cp.zeros_like(v)
    w = _matvec(v)
    print(f"w_{i} = {w}")
    print(f"ev_{i} * v_{i} = {ev*v}")
    error = cp.linalg.norm(w - ev * v) / cp.linalg.norm(w)
    print(f"相对误差: {error:.2e}")
    j = i+1
    if i == len(_eigenvalues)-1:
        j = 0
    eigen_diff = cp.linalg.norm(
        _eigenvectors[i]-_eigenvectors[j])/cp.linalg.norm(_eigenvectors[i])
    print(f"本征向量{i}与本征向量{j}的相对误差:{eigen_diff:.2e}")

λ_0 = 0.00064802-0.00000000j
v_0 = [0.0002671 +0.00033389j 0.00026914+0.0003151j  0.00023126+0.00029412j ...
 0.00031721+0.00026323j 0.00030408+0.00028839j 0.00029509+0.00026849j]
norm src 1.0
norm dest 0.00069020095
w_0 = [1.6576905e-07+1.24277904e-07j 2.1579626e-07+1.10508154e-07j
 2.4217297e-07+9.54200914e-08j ... 2.1075675e-07+2.12674422e-07j
 2.1949290e-07+2.42019269e-07j 1.8068113e-07+2.17118213e-07j]
ev_0 * v_0 = [1.7308527e-07+2.1637089e-07j 1.7440651e-07+2.0419223e-07j
 1.4986290e-07+1.9059557e-07j ... 2.0555639e-07+1.7058044e-07j
 1.9704842e-07+1.8688175e-07j 1.9122251e-07+1.7398902e-07j]
相对误差: 3.44e-01
本征向量0与本征向量1的相对误差:1.43e+00
λ_1 = 0.00068879+0.00000000j
v_1 = [0.00028195+4.8963167e-04j 0.00023728+5.5122568e-04j
 0.00019183+5.4973154e-04j ... 0.00023719+9.2579130e-06j
 0.00024886+1.4722072e-05j 0.00025686+2.9678380e-05j]
norm src 0.9999999
norm dest 0.0009370313
w_1 = [2.5829013e-07+1.76008143e-07j 2.7359738e-07+2.15954060e-07j
 2.5902909e-07+2.19702997e-07j ... 2.3249822e

In [74]:
# import numpy as np

# def min_eigenvalue_power_iteration(A, num_iterations=100, tolerance=1e-10):
#     """
#     使用幂迭代法计算矩阵的最小本征值

#     参数:
#         A: numpy数组，输入矩阵（方阵）
#         num_iterations: 最大迭代次数
#         tolerance: 收敛容差

#     返回:
#         min_eigenvalue: 最小本征值的估计值
#         min_eigenvector: 对应的本征向量
#     """
#     # 计算矩阵的最大绝对本征值（用于位移变换）
#     n = A.shape[0]
#     v = np.random.rand(n)
#     max_eigenvalue = power_iteration(A, num_iterations, tolerance)[0]

#     # 进行位移变换：B = max_eigenvalue * I - A
#     # 这样B的最大本征值对应A的最小本征值
#     I = np.eye(n)
#     B = max_eigenvalue * I - A

#     # 对变换后的矩阵使用标准幂迭移法
#     v = np.random.rand(n)
#     v = v / np.linalg.norm(v)

#     for i in range(num_iterations):
#         v_old = v.copy()

#         # 幂迭代步骤
#         v = B @ v
#         v = v / np.linalg.norm(v)

#         # 检查收敛性
#         if np.allclose(v, v_old, rtol=tolerance):
#             break

#     # 计算最小本征值
#     min_eigenvalue = max_eigenvalue - (v.T @ B @ v) / (v.T @ v)

#     return min_eigenvalue, v

# def power_iteration(A, num_iterations=100, tolerance=1e-10):
#     """
#     标准幂迭代法计算最大本征值
#     """
#     n = A.shape[0]
#     v = np.random.rand(n)
#     v = v / np.linalg.norm(v)

#     for i in range(num_iterations):
#         v_old = v.copy()
#         v = A @ v
#         v = v / np.linalg.norm(v)

#         if np.allclose(v, v_old, rtol=tolerance):
#             break

#     eigenvalue = (v.T @ A @ v) / (v.T @ v)
#     return eigenvalue, v

# # 测试代码
# if __name__ == "__main__":
#     # 创建一个对称矩阵进行测试
#     A = np.array([[4, -1, 0],
#                   [-1, 4, -1],
#                   [0, -1, 4]])

#     min_eval, min_evec = min_eigenvalue_power_iteration(A)
#     print(f"最小本征值: {min_eval:.6f}")
#     print(f"对应的本征向量: {min_evec}")

#     # 验证结果
#     true_eigenvalues = np.linalg.eigvals(A)
#     print(f"numpy计算的所有本征值: {true_eigenvalues}")
#     print(f"实际最小本征值: {min(true_eigenvalues.real):.6f}")

In [75]:
# qcu.applyEndQcu(set_ptrs, params)